# Reccommendation System

### Scenario

You joined as the new memeber of a small start-up team. Together we are building a new app to sell cool 3rd party products! So far, the sales team worked tirelessly and managed to acquire over 50 merchants who each have different brands and products offerings. The developers have made a ton of progress on the mobile app and there's a bunch of user activity on the app. The analytics platform Mixpanel is used to collect all the user event data. The next step is to optimize user conversion rates by offering new recommendations based on the analytics data.

### Goal

Your task is to recommend a product that a user is most likely to buy next using the purchase history provided.

For the purpose of this interview test, we have provided mock data on customer purchase history from an e-commerce retail company. The 'Purchased Product' events were queried through Mixpanel's API and is exported into the file training_mixpanel.txt, as provided, in JSON format. Each event describes a singular product purchased by a particular user, with descriptive attributes of the product (e.g., quantity, unit price). Transactions purchasing multiple products is denoted by invoice_no.

### Action

Let's start by first importing all the necessary libraries. We should then explore the dataset to get an intuitive understanding of what we're working with.

## 0. Import Libraries

In [1]:
import numpy as np
import pandas as pd
import scipy
import math
import random
import sklearn
import json
import nltk 

import matplotlib.pyplot as plt
%matplotlib inline

from nltk.corpus import stopwords
from sklearn.metrics import roc_auc_score
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from scipy.sparse.linalg import svds

## 1. Data Exploration

In [2]:
filename = "training_mixpanel.txt"

with open(filename) as f: 
    python_obj = json.load(f)

So we can see that the data set is a collection of events, all of them are a product being purchased. The event has properties such as invoice number, product id, description, quantity, invoice date, unit price, customer id, and country. 

The customer id is our user. We can manipulate this data set in a variety of ways to gain some useful information on how best to approach this problem. 

How often was a product bought? 
How many different products did each user buy?
Where were most of the products bought from? 
what time of day were the products brought at?

All these may seem unrelated but can produce meaningful insights down the road. 

In [3]:
print (json.dumps(python_obj[0], sort_keys=True, indent=4)) #pretty printing

{
    "event": "Purchased Product",
    "properties": {
        "country": "United Kingdom",
        "customer_id": 17850,
        "description": "WHITE HANGING HEART T-LIGHT HOLDER",
        "invoice_date": "12/1/2010 8:26",
        "invoice_no": "536365",
        "product_id": "85123A",
        "quantity": 6,
        "unit_price": 2.55
    }
}


### We move over to pandas to visualize and manipulate our data

As all data is purchases, we can collect solely the properties 

In [4]:
properties = []
for i in range(len(python_obj)):
    properties.append(python_obj[i].get('properties'))

In [5]:
prop = pd.DataFrame(properties)  #Creating a DataFrame for our data
prop

country  customer_id                          description  \
0       United Kingdom        17850   WHITE HANGING HEART T-LIGHT HOLDER   
1       United Kingdom        17850                  WHITE METAL LANTERN   
2       United Kingdom        17850         SET 7 BABUSHKA NESTING BOXES   
3       United Kingdom        17850    GLASS STAR FROSTED T-LIGHT HOLDER   
4       United Kingdom        17850               HAND WARMER UNION JACK   
5       United Kingdom        17850            HAND WARMER RED POLKA DOT   
6       United Kingdom        13047        ASSORTED COLOUR BIRD ORNAMENT   
7       United Kingdom        13047           POPPY'S PLAYHOUSE BEDROOM    
8       United Kingdom        13047            POPPY'S PLAYHOUSE KITCHEN   
9       United Kingdom        13047    FELTCRAFT PRINCESS CHARLOTTE DOLL   
10      United Kingdom        13047              IVORY KNITTED MUG COSY    
11      United Kingdom        13047   BOX OF 6 ASSORTED COLOUR TEASPOONS   
12      United Kingdom        13047        BOX OF VINTAGE JIGSAW BLOCKS    
13      United Kingdom        13047             HOME BUILDING BLOCK WORD   
14      United Kingdom        13047             LOVE BUILDING BLOCK WORD   
15      United Kingdom        13047          RECIPE BOX WITH METAL HEART   
16      United Kingdom        13047             JAM MAKING SET WITH JARS   
17      United Kingdom        13047          RED COAT RACK PARIS FASHION   
18      United Kingdom        13047         BLUE COAT RACK PARIS FASHION   
19      United Kingdom        13047             BATH BUILDING BLOCK WORD   
20              France        12583            ALARM CLOCK BAKELIKE PINK   
21              France        12583            ALARM CLOCK BAKELIKE RED    
22              France        12583           ALARM CLOCK BAKELIKE GREEN   
23              France        12583      PANDA AND BUNNIES STICKER SHEET   
24              France        12583                     STARS GIFT TAPE    
25              France        12583          INFLATABLE POLITICAL GLOBE    
26              France        12583   VINTAGE HEADS AND TAILS CARD GAME    
27              France        12583      SET/2 RED RETROSPOT TEA TOWELS    
28              France        12583  ROUND SNACK BOXES SET OF4 WOODLAND    
29              France        12583                  SPACEBOY LUNCH BOX    
...                ...          ...                                  ...   
322845  United Kingdom        15804      VICTORIAN GLASS HANGING T-LIGHT   
322846  United Kingdom        15804       EMBOSSED GLASS TEALIGHT HOLDER   
322847  United Kingdom        15804     ZINC WILLIE WINKIE  CANDLE STICK   
322848  United Kingdom        15804                   RABBIT NIGHT LIGHT   
322849  United Kingdom        15804        ASSORTED COLOUR BIRD ORNAMENT   
322850  United Kingdom        15804   MULTI COLOUR SILVER T-LIGHT HOLDER   
322851  United Kingdom        15804           ALARM CLOCK BAKELIKE GREEN   
322852  United Kingdom        15804          LARGE CHINESE STYLE SCISSOR   
322853  United Kingdom        15804      SET 12 RETRO WHITE CHALK STICKS   
322854  United Kingdom        15804          BOX OF 24 COCKTAIL PARASOLS   
322855  United Kingdom        15804         ANTIQUE SILVER T-LIGHT GLASS   
322856  United Kingdom        15804     SMALL MEDINA STAMPED METAL BOWL    
322857  United Kingdom        15804           MAGNETS PACK OF 4 SWALLOWS   
322858  United Kingdom        15804       ZINC T-LIGHT HOLDER STAR LARGE   
322859  United Kingdom        15804       FAIRY TALE COTTAGE NIGHT LIGHT   
322860  United Kingdom        13113     SET OF 3 HANGING OWLS OLLIE BEAK   
322861  United Kingdom        13113        RED RETROSPOT ROUND CAKE TINS   
322862          France        12680             CIRCUS PARADE LUNCH BOX    
322863          France        12680       PLASTERS IN TIN CIRCUS PARADE    
322864          France        12680            PLASTERS IN TIN STRONGMAN   
322865          France        12680            ALARM CLOCK BAKE

In [6]:
print(len(pd.value_counts(prop["customer_id"])))

4363


In [7]:
print(len(pd.value_counts(prop["product_id"])))

3677


4636 unique users and 3677 unique products

In [8]:
prop.describe()

customer_id       quantity     unit_price
count  322875.000000  322875.000000  322875.000000
mean    15285.738180      12.103250       2.934132
std      1712.664883     278.315144       6.228682
min     12346.000000  -80995.000000       0.000000
25%     13952.000000       2.000000       1.250000
50%     15150.000000       5.000000       1.950000
75%     16788.000000      12.000000       3.750000
max     18287.000000   80995.000000    1100.440000

It would be great to compute the rate of return of an item and include that in our calculations. 
Pursuing a popularity based approach could see some improvements from this as well as further narrowing down based on location.

However, for a collaborative filter and content based filter, it's mostly just the purchases that influence our recommendation. 

In [9]:
prop = prop[prop['quantity']>0] #removes negative values i.e. returns
prop.describe()

customer_id       quantity     unit_price
count  315955.000000  315955.000000  315955.000000
mean    15292.471308      13.161225       2.876110
std      1712.436354     201.343614       4.399119
min     12346.000000       1.000000       0.000000
25%     13969.000000       2.000000       1.250000
50%     15157.000000       6.000000       1.950000
75%     16794.000000      12.000000       3.750000
max     18287.000000   80995.000000     649.500000

In [10]:
print(len(pd.value_counts(prop["customer_id"])))

4335


In [11]:
print(len(pd.value_counts(prop["product_id"])))

3659


So it appears that there were some items that have only been returns in the dataset, likewise some users that have only returned items in the dataset. We could mark the returns as once purchases or just clean the data by discarding them from the data set and recommending users with overall positive item interactions.

### Let's multiply the quantity with unit price to get a weighted strength score. We might want to give good recommendations of most products bought but we also want to increase our revenue! 

In [12]:
value = prop.quantity * prop.unit_price
#Scale our results with log so the data set isn't skewewd by a few large purchases
value_scaled = np.log2(1+value)  ## add one so that values below 1 don't push us back negative and zero values don't put as -inf
prop['value'] = value_scaled
prop['quantityScaled'] = np.log(prop.quantity) #Perhaps nominal quantity is a better measure without economics playing a part
prop

C:\Users\Prakash14\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.
C:\Users\Prakash14\Anaconda3\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """


country  customer_id                          description  \
0       United Kingdom        17850   WHITE HANGING HEART T-LIGHT HOLDER   
1       United Kingdom        17850                  WHITE METAL LANTERN   
2       United Kingdom        17850         SET 7 BABUSHKA NESTING BOXES   
3       United Kingdom        17850    GLASS STAR FROSTED T-LIGHT HOLDER   
4       United Kingdom        17850               HAND WARMER UNION JACK   
5       United Kingdom        17850            HAND WARMER RED POLKA DOT   
6       United Kingdom        13047        ASSORTED COLOUR BIRD ORNAMENT   
7       United Kingdom        13047           POPPY'S PLAYHOUSE BEDROOM    
8       United Kingdom        13047            POPPY'S PLAYHOUSE KITCHEN   
9       United Kingdom        13047    FELTCRAFT PRINCESS CHARLOTTE DOLL   
10      United Kingdom        13047              IVORY KNITTED MUG COSY    
11      United Kingdom        13047   BOX OF 6 ASSORTED COLOUR TEASPOONS   
12      United Kingdom        13047        BOX OF VINTAGE JIGSAW BLOCKS    
13      United Kingdom        13047             HOME BUILDING BLOCK WORD   
14      United Kingdom        13047             LOVE BUILDING BLOCK WORD   
15      United Kingdom        13047          RECIPE BOX WITH METAL HEART   
16      United Kingdom        13047             JAM MAKING SET WITH JARS   
17      United Kingdom        13047          RED COAT RACK PARIS FASHION   
18      United Kingdom        13047         BLUE COAT RACK PARIS FASHION   
19      United Kingdom        13047             BATH BUILDING BLOCK WORD   
20              France        12583            ALARM CLOCK BAKELIKE PINK   
21              France        12583            ALARM CLOCK BAKELIKE RED    
22              France        12583           ALARM CLOCK BAKELIKE GREEN   
23              France        12583      PANDA AND BUNNIES STICKER SHEET   
24              France        12583                     STARS GIFT TAPE    
25              France        12583          INFLATABLE POLITICAL GLOBE    
26              France        12583   VINTAGE HEADS AND TAILS CARD GAME    
27              France        12583      SET/2 RED RETROSPOT TEA TOWELS    
28              France        12583  ROUND SNACK BOXES SET OF4 WOODLAND    
29              France        12583                  SPACEBOY LUNCH BOX    
...                ...          ...                                  ...   
322845  United Kingdom        15804      VICTORIAN GLASS HANGING T-LIGHT   
322846  United Kingdom        15804       EMBOSSED GLASS TEALIGHT HOLDER   
322847  United Kingdom        15804     ZINC WILLIE WINKIE  CANDLE STICK   
322848  United Kingdom        15804                   RABBIT NIGHT LIGHT   
322849  United Kingdom        15804        ASSORTED COLOUR BIRD ORNAMENT   
322850  United Kingdom        15804   MULTI COLOUR SILVER T-LIGHT HOLDER   
322851  United Kingdom        15804           ALARM CLOCK BAKELIKE GREEN   
322852  United Kingdom        15804          LARGE CHINESE STYLE SCISSOR   
322853  United Kingdom        15804      SET 12 RETRO WHITE CHALK STICKS   
322854  United Kingdom        15804          BOX OF 24 COCKTAIL PARASOLS   
322855  United Kingdom        15804         ANTIQUE SILVER T-LIGHT GLASS   
322856  United Kingdom        15804     SMALL MEDINA STAMPED METAL BOWL    
322857  United Kingdom        15804           MAGNETS PACK OF 4 SWALLOWS   
322858  United Kingdom        15804       ZINC T-LIGHT HOLDER STAR LARGE   
322859  United Kingdom        15804       FAIRY TALE COTTAGE NIGHT LIGHT   
322860  United Kingdom        13113     SET OF 3 HANGING OWLS OLLIE BEAK   
322861  United Kingdom        13113        RED RETROSPOT ROUND CAKE TINS   
322862          France        12680             CIRCUS PARADE LUNCH BOX    
322863          France        12680       PLASTERS IN TIN CIRCUS PARADE    
322864          France        12680            PLASTERS IN TIN STRONGMAN   
322865          France        12680            ALARM CLOCK BAKE

The log transformation here converts our values at zero to -inf. By setting these values to zero we can make sure that people who have returned more than they have bought don't influence our collaborative filter. 

In [13]:
prop = prop.drop_duplicates() #let's drop duplicate rows
prop.describe()

customer_id       quantity     unit_price          value  \
count  311884.000000  311884.000000  311884.000000  311884.000000   
mean    15286.186287      13.297729       2.881865       3.555415   
std      1712.707014     202.647578       4.419935       1.458827   
min     12346.000000       1.000000       0.000000       0.000000   
25%     13952.000000       2.000000       1.250000       2.572890   
50%     15150.000000       6.000000       1.950000       3.689299   
75%     16790.000000      12.000000       3.750000       4.378512   
max     18287.000000   80995.000000     649.500000      17.362137   

       quantityScaled  
count   311884.000000  
mean         1.668988  
std          1.204810  
min          0.000000  
25%          0.693147  
50%          1.791759  
75%          2.484907  
max         11.302143

In the meantime lets create a separate datafiles aggregated with the values we want

In [ ]:
Purchases_df = prop.groupby(['customer_id', 'product_id'])['value'].sum().reset_index()
print('# of unique customer/item purchases: %d' % len(PurchasesN_df))
PurchasesN_df.head(10)

Completely skews our data set. Perhaps better not to include the returns as well so that the we're not recommending to users products that have high return rates. 

### All counts of transactions below includes returns (counted twice)

We have 4363 unique users who have on average bought 74 items. Someone who has bought over 6000 items! Say, a median of 33 is probably a better indicator of the number of products a user usually purchases. 

In [ ]:
#user_purchases[user_purchases<5]

About 300 users who have bought less than 5 items. How do you recommend products to those? 

Conventionally, we have several approaches (in descending order of robustness): 
    1. Cross-domain information: Users who bought this also bought
    2. Personality information: Similar personalities have similar interests
    3. Content-based recommendation: hybridized with collaborative
    4. Preference elicitation: Asking user preferences directly Think Kindle
    5. Popularity based recommendation: Simply what's popular:
        Can use time of day, time of year, and/or geographical location further to focus the popularity based appraoch
     

In [ ]:
user_purchases[user_purchases>5].hist(bins=100)
#product_purchases.hist(bins=10)
#sns.distplot(product_purchases[product_purchases <=20], kde = False, bins = 20)

#plt.hist(product_purchases, bins=bins, alpha = 0.5)

There's a very few set of users buying so many things they may skew our model to impart their preferences onto the rest. 

In [ ]:

#print(('products with no record of purchase, but that have been returned:', properties['product_id'].nunique() - properties.loc[properties['quantity'] >= 0]['product_id'].nunique())
#print('customers with no record of purchase, but that have returned items:', properties['customer_id'].nunique() - properties.loc[properties['quantity'] >= 0]['customer_id'].nunique())

### The below method is to identify number of unique transactions that won't count returns twice (doesn't include quantity of items bought)

In [ ]:
User_purchases_df = prop.groupby(['customer_id', 'product_id']).size().reset_index() #Mapping the number of times a customer has bought a specific product
User_purchases_df = User_purchases_df.groupby('customer_id').size()#Reduces to the number of users that have made unique product purchases
User_purchases_df.head()
#print('# users: %d' % len(purchases_df))

In [ ]:
Product_purchases_df = prop.groupby(['customer_id', 'product_id']).size()
Product_purchases_df = Product_purchases_df.groupby('product_id').size().reset_index()
Product_purchases_df.describe()
#Product_purchases_df.head()

Creating a data file that has unique customer-item purchases without returns

There were probably a few interactions that were only returns. This DF doesn't contain that.

In [ ]:
Purchases_df.describe()

So most items have been returned by the users, the item that one single user bought the most units of without returning was 64.

In [16]:
Purchases_df = prop.groupby(['customer_id', 'product_id'])['value'].mean().reset_index()
print('# of unique customer/item purchases: %d' % len(Purchases_df))
Purchases_df.head(10)


# of unique customer/item purchases: 212995


customer_id product_id      value
0        12346      23166  16.236025
1        12347      16008   2.807355
2        12347      17021   3.560715
3        12347      20665   4.224966
4        12347      20719   3.247928
5        12347      20780   5.827819
6        12347      20782   5.084915
7        12347      20966   3.754888
8        12347      21035   4.224966
9        12347      21041   4.224966

In [17]:
Purchases_df.describe()

customer_id          value
count  212995.000000  212995.000000
mean    15273.910899       3.490932
std      1710.864276       1.345601
min     12346.000000       0.000000
25%     13862.000000       2.572890
50%     15214.000000       3.666757
75%     16771.000000       4.238515
max     18287.000000      17.362137

## 2. Data Pre-processing

First thing to always do in the ML preprocessing pipeline is to split the dataset. 

If this step is done later on, we would have applied our model over the whole dataset and fit really well on it and would be testing ourselves again on the evaluated data. Like asking darth vader if hes evil and he says no hes not evil so we believe him. 

In [ ]:
training_purchases, testing_purchases = train_test_split(Purchases_df, test_size = 0.2)  

print('# of training purchases: %d' % len(training_purchases))
print('# of testing purchases: %d' % len(testing_purchases))

In [19]:
#Indexing by personId to speed up the searches during evaluation
purchases_full_indexed_df = Purchases_df.set_index('customer_id')
#training_indexed_df = training_purchases.set_index('customer_id')
#testing_indexed_df = testing_purchases.set_index('customer_id')

In [20]:
purchases_full_indexed_df

product_id      value
customer_id                      
12346            23166  16.236025
12347            16008   2.807355
12347            17021   3.560715
12347            20665   4.224966
12347            20719   3.247928
12347            20780   5.827819
12347            20782   5.084915
12347            20966   3.754888
12347            21035   4.224966
12347            21041   4.224966
12347            21064   5.075952
12347            21154   3.754888
12347            21171   4.201634
12347            21265   4.608809
12347            21578   3.857981
12347            21636   3.321928
12347            21731   4.571491
12347            21791   4.318065
12347            21832   4.378512
12347            21975   3.827819
12347            21976   3.827819
12347            22131   3.666757
12347            22134   2.594549
12347            22195   4.700144
12347            22196   3.952483
12347            22212   3.765535
12347            22252   4.000000
12347            22371   5.006357
12347            22372   4.169925
12347            22374   4.489711
...                ...        ...
18287            22603   4.419539
18287            22644   4.201634
18287            22752   5.129283
18287            22753   3.485427
18287            22754   3.485427
18287            22755   3.485427
18287            22756   4.000000
18287            22758   4.000000
18287            22807   4.224966
18287            22865   4.711495
18287            22866   4.711495
18287            23076   4.954196
18287            23078   4.954196
18287            23223   5.351911
18287            23264   4.761781
18287            23267   4.954196
18287            23269   5.733354
18287            23272   4.378512
18287            23376   4.301588
18287            23378   3.372952
18287            23445   4.137504
18287            35967   3.875780
18287            47422   3.469886
18287           72349B   5.535578
18287           72351A   5.683696
18287           84507C   4.026800
18287            84584   4.026800
18287            84920   4.000000
18287           85039A   6.141596
18287           85040A   5.147494

[212995 rows x 2 columns]

## Popularity

 We can see a few negative values here and there. Let's remove them first

In [ ]:
mask = prop.quantity > 0
propN = prop[mask] 
propN.describe()

In [ ]:
# compute the most popular items
item_popularity_returns_absolute = propN.groupby('product_id')['quantity'].sum().sort_values(ascending=False).reset_index()
item_popularity_returns_absolute.head(10)

Our 10 most popular items! With returns taken into account. 

Without return taken into account

However these are absolute numbers. What if we checked the highest purchases against their return rate?

In [72]:
item_popularity_df = prop.groupby('customer_id')['quantity'].mean().sort_values(ascending=False).reset_index()
item_popularity_df.describe()

customer_id      quantity
count   4363.000000   4363.000000
mean   15299.772863     22.895145
std     1721.852042    213.474098
min    12346.000000   -144.000000
25%    13813.500000      5.485357
50%    15299.000000      9.566038
75%    16777.500000     14.240000
max    18287.000000  12540.000000

The mean of the products purchased takes into account the returns as well and gives us the products that have the highest number of purchases that have been satisfactoraliy kept and used by our users.

In [ ]:
class PopularityRecommender: 
    model_name = 'Popularity'
    
    def _init_(self, popularity_df, items_df=None):
        self.popularity_df = popularity_df
        self.items_df=items_df
        
    def get_model_name(self):
        return self.model_name
    
    def recommend_items(self, user_id, items_to_ignore=[], topn=10):
        #Recommend the most popular items that the user hasn't seen yet
        recommendations_df = self.popularity_df[~self.popularity_df['product_id'].isin(items_to_ignore)].sort_values('eventStrength',ascending = False).head(topn)
        
        

## Content Based Filtering

In [33]:
print(len(pd.value_counts(prop["product_id"])))

3659


In [34]:
print(len(pd.value_counts(prop["description"])))

3860


There seems to be 3659 unique product ids, but 3860 unique product descriptions. 

So there must be a product id with two different descriptions. We'll just focus on our product ids and discard the extra discriptions.

In [35]:
collab_df = prop.drop_duplicates('product_id')
len(collab_df)
collab_df.head()

country  customer_id                         description  \
0  United Kingdom        17850  WHITE HANGING HEART T-LIGHT HOLDER   
1  United Kingdom        17850                 WHITE METAL LANTERN   
2  United Kingdom        17850        SET 7 BABUSHKA NESTING BOXES   
3  United Kingdom        17850   GLASS STAR FROSTED T-LIGHT HOLDER   
4  United Kingdom        17850              HAND WARMER UNION JACK   

     invoice_date invoice_no product_id  quantity  unit_price     value  \
0  12/1/2010 8:26     536365     85123A         6        2.55  4.026800   
1  12/1/2010 8:26     536365      71053         6        3.39  4.415488   
2  12/1/2010 8:26     536365      22752         2        7.65  4.026800   
3  12/1/2010 8:26     536365      21730         6        4.25  4.727920   
4  12/1/2010 8:28     536366      22633         6        1.85  3.596935   

   quantityScaled  
0        1.791759  
1        1.791759  
2        0.693147  
3        1.791759  
4        1.791759

In [36]:
from sklearn.metrics.pairwise import linear_kernel
#color = (['WHITE', 'BLACK', 'BLUE', "RED", 'GREEN', 'YELLOW', 'ORANGE', 'PURPLE', 'INDIGO'])
stopwords_list = stopwords.words('english') 

vectorizer = TfidfVectorizer(analyzer = 'word',
                           ngram_range=(1,2),
                           min_df=0.0003,
                           max_df=0.5,
                           max_features = None,
                           lowercase=True,
                           stop_words=stopwords_list)
item_ids = prop['product_id'].drop_duplicates().tolist()
tfidf_matrix = vectorizer.fit_transform(collab_df['description'])
tfidf_feature_names = vectorizer.get_feature_names()
#cosine_similarities = linear_kernel(tfidf_matrix, tfidf_matrix)
tfidf_matrix

<3659x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 21055 stored elements in Compressed Sparse Row format>

Let's have a look at our features:

In [37]:
tfidf_feature_names

['10',
 '12',
 '12 blue',
 '12 colour',
 '12 coloured',
 '12 kids',
 '12 mini',
 '12 pencils',
 '12 pink',
 '12 red',
 '12 vintage',
 '120cm',
 '15',
 '15cm',
 '16',
 '16 vintage',
 '20',
 '20 dolly',
 '20 napkins',
 '200',
 '20light',
 '24',
 '30cm',
 '36',
 '36 colour',
 '36 doilies',
 '36 foil',
 '36 pencils',
 '3d',
 '3d sheet',
 '40',
 '40 cones',
 '42',
 '42 neckl',
 '45cm',
 '50',
 '50 christmas',
 '50 pieces',
 '60',
 '60 cake',
 '60cm',
 '70',
 '70 tray',
 '72',
 '72 retrospot',
 '72 skull',
 '75',
 '75 green',
 'a4',
 'a4 wall',
 'a6',
 'a6 size',
 'a7',
 'a7 size',
 'abstract',
 'abstract circles',
 'acapulco',
 'acapulco mat',
 'acrylic',
 'acrylic edwardian',
 'acrylic faceted',
 'acrylic hanging',
 'acrylic jewel',
 'advent',
 'advent calendar',
 'aid',
 'aid tin',
 'airline',
 'airline bag',
 'alarm',
 'alarm clock',
 'album',
 'alphabet',
 'alphabet design',
 'alphabet iron',
 'amber',
 'amber chunky',
 'amber drop',
 'amber glass',
 'amethyst',
 'anemone',
 'anemone ar

In [38]:
cosine_similarities_item = linear_kernel(tfidf_matrix, tfidf_matrix)
cosine_similarities_item

array([[1.        , 0.09163842, 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.09163842, 1.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 1.        , ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.        , 0.        , 0.        , ..., 1.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 1.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        1.        ]])

Now, to model the user profile, we take all the item profiles the user has bought and average them. 

In [39]:
def get_item_profile(item_id):
    """Obtains a vector profiling an item"""
    print(item_id)
    idx = item_ids.index(item_id)
    #print(idx)
    item_profile = tfidf_matrix[idx:idx+1] #The 1000 element row vector for the item
    return item_profile

def get_item_profiles(ids):
    """Get all the item profiles for a given list of items"""
    if type(ids)==str:
        print (len(ids))
        ids = [ids] #if isinstance(ids, list) else [ids] #to make sure we are always dealing with lists, even when a single element
    
    print(len(ids))
    item_profiles_list = [get_item_profile(x) for x in ids] #get all the items
        
    item_profiles = scipy.sparse.vstack(item_profiles_list) #stack them on top of each other
    return item_profiles

def build_users_profile(customer_id, purchases_full_indexed_df): 
    """Get all the"""
    purchases_customer_df = purchases_full_indexed_df.loc[customer_id] #Receive the customer id and log all their purchases
    user_item_profiles = get_item_profiles(purchases_customer_df['product_id'])
    user_profile_norm = sklearn.preprocessing.normalize(user_item_profiles)
    #print(user_item_profiles)
    return user_item_profiles

def build_users_profiles():
    #purchases_full_indexed_df = Purchases_df.set_index('customer_id')
    user_profiles = {}
    for user_id in purchases_full_indexed_df.index.unique():
        user_profiles[user_id] = build_users_profile(user_id,purchases_full_indexed_df)
        
    return user_profiles

In [40]:
user_profiles = build_users_profiles()
#user_profiles

5
1
23166
103
16008
17021
20665
20719
20780
20782
20966
21035
21041
21064
21154
21171
21265
21578
21636
21731
21791
21832
21975
21976
22131
22134
22195
22196
22212
22252
22371
22372
22374
22375
22376
22417
22422
22423
22432
22492
22494
22497
22550
22561
22621
22697
22698
22699
22725
22726
22727
22728
22729
22771
22772
22773
22774
22775
22805
22821
22945
22992
23076
23084
23146
23147
23162
23170
23171
23172
23173
23174
23175
23177
23271
23297
23308
23316
23420
23421
23422
23480
23497
23503
23506
23508
23552
47559B
47567B
47580
51014C
71477
84558A
84559A
84559B
84625A
84625C
84969
84991
84992
84997B
84997C
84997D
85116
85167B
85178
85232D
20
21211
21213
21725
21726
21967
21977
21980
21981
21982
21983
21985
22437
22616
22951
22952
23076
23077
23078
84988
84991
72
20685
20914
21086
21136
21231
21232
21411
21531
21533
21535
21563
21564
21787
22059
22064
22070
22071
22131
22195
22326
22333
22423
22430
22441
22553
22554
22555
22556
22557
22567
22601
22666
22692
22704
22720
22722
22832
22960
2

23354
23497
23571
46775D
72741
84992
85174
13
20712
20713
20719
20749
21929
21930
22355
22356
23200
23203
84997C
84997D
85099C
55
16012
20662
20750
20856
21080
21206
21365
21380
21506
21561
21680
21721
21832
21871
21877
22021
22029
22037
22090
22107
22108
22109
22112
22190
22300
22301
22302
22303
22314
22328
22422
22448
22449
22538
22540
22545
22546
22551
22555
22556
22631
22713
22716
22725
22726
22727
22728
22729
22730
22837
22953
37495
84050
84997D
85206A
187
15058B
16161U
20674
20675
20686
20725
20750
20754
21039
21078
21080
21094
21098
21114
21154
21188
21201
21205
21208
21212
21238
21240
21242
21243
21244
21245
21288
21537
21556
21558
21559
21561
21668
21671
21672
21706
21707
21709
21731
21936
21967
21981
21982
21985
21987
21988
21989
22074
22075
22148
22189
22254
22255
22273
22313
22318
22320
22325
22326
22328
22329
22332
22333
22334
22365
22371
22374
22383
22384
22430
22431
22434
22435
22436
22452
22532
22535
22550
22583
22584
22585
22588
22589
22602
22605
22615
22619
22628
2262

23190
23192
23194
23201
23202
23203
23206
23208
23209
23230
23231
23232
23233
23234
23235
23236
23238
23239
23240
23241
23242
23243
23245
23247
23253
23254
23255
23256
23283
23285
23286
23287
23288
23291
23292
23293
23294
23295
23296
23297
23298
23299
23300
23306
23307
23309
23312
23314
23326
23327
23328
23340
23341
23342
23343
23345
23346
23347
23349
23360
23371
23372
23382
23389
23392
23436
23445
23497
23502
23505
23507
23510
23512
23513
23515
23516
23518
23523
23524
23525
23526
23527
23533
23534
23541
23542
23545
23550
37370
47566
47590A
47590B
48138
48194
79191C
84029G
84218
84228
84509A
84519A
84519B
84944
84992
84997B
84997D
85014A
85014B
85071A
85071B
85071C
85099B
85132A
85183B
138
16161P
16169M
20971
21042
21080
21084
21090
21135
21212
21218
21249
21257
21318
21430
21452
21467
21481
21499
21500
21578
21672
21673
21700
21717
21770
21843
21974
21977
22040
22060
22071
22138
22168
22169
22214
22222
22223
22236
22261
22303
22398
22417
22423
22501
22619
22623
22624
22625
22644
22666

23029
23031
23032
23034
23074
23110
23112
23118
23160
23164
23165
23169
23171
23172
23175
23176
23245
23311
23330
23333
23394
23400
23404
23413
23418
23425
23479
23482
23564
35810A
46000M
46000S
72807C
82482
82484
82494L
82551
84279P
84378
84817
84819
84820
84832
84843
84879
85053
85059
85132C
85231B
3
23497
85034B
85034C
46
20676
20718
20725
21238
21242
21340
21580
21889
22138
22139
22178
22380
22381
22384
22423
22467
22508
22526
22605
22619
22620
22625
22666
22727
22960
23081
23169
23201
23203
23205
23209
23240
23245
23284
23298
23348
23395
23407
23469
47566
47590B
47591D
48138
84375
85066
85099B
19
20674
20676
20712
20749
20750
21238
21242
21245
21531
21533
21535
22303
22326
22551
22556
22628
22631
22659
85099B
16
21084
21090
21155
21212
21558
22367
22402
22471
22553
22557
22585
22630
22899
46000M
48184
85019B
101
18007
20665
20724
20725
20749
20750
20764
20766
20770
20914
20979
21165
21216
21218
21285
21559
21731
21770
21787
21791
21844
21889
21906
21908
21912
21914
21915
21935
220

21531
21535
21539
21559
21563
21564
21668
21669
21672
21707
21877
21880
21908
21935
21936
22070
22077
22111
22123
22168
22173
22193
22200
22203
22207
22212
22243
22244
22260
22262
22278
22303
22304
22325
22329
22352
22354
22365
22366
22378
22379
22414
22446
22447
22449
22453
22467
22482
22507
22626
22637
22689
22692
22721
22722
22723
22781
22805
22832
22840
22894
22896
22897
22900
22979
22989
22990
23107
23110
23146
23154
23155
23156
23158
23159
23179
23199
23235
23240
23243
23244
23245
23287
23393
23396
23402
23406
35241
35598D
35599B
44242B
47585A
48129
48138
48173C
48184
82482
82486
82578
82580
84029E
84050
84347
84356
84406B
84687
84792
84968A
84968C
84968D
84968E
84997B
85099B
25
20685
20725
20727
20728
20750
21479
21481
22037
22138
22139
22327
22382
22617
22619
22623
22712
22816
22899
22940
22941
23084
23108
23256
23389
23390
24
20973
20978
20979
21080
21088
21094
21210
21212
21216
21217
21882
21987
21988
21989
22077
22215
22437
22720
22993
23243
23370
84992
85049C
85049E
105
161

...

22816
22951
22970
22972
22996
23128
23232
23233
23308
23309
23318
23356
84077
5
22481
22988
23203
72803A
84813
22
16011
20856
21395
22139
22466
22529
22531
22535
22566
22743
22744
22746
22747
22748
22756
22758
22907
23084
23192
23239
84378
84497
176
11001
15034
15036
16168M
16238
17003
20615
20676
20682
20727
20728
20956
20969
20978
21034
21080
21086
21090
21094
21096
21110
21114
21126
21161
21187
21192
21198
21199
21240
21244
21326
21391
21479
21528
21530
21664
21698
21703
21706
21820
21821
21833
21870
21874
21876
21877
21890
21891
21906
21914
21915
21916
21989
22093
22100
22162
22197
22219
22227
22271
22274
22276
22310
22317
22327
22333
22358
22371
22374
22375
22377
22378
22379
22382
22383
22384
22399
22411
22418
22419
22427
22428
22431
22432
22439
22443
22444
22457
22461
22473
22475
22492
22493
22508
22513
22519
22521
22525
22537
22582
22583
22584
22606
22608
22619
22620
22621
22624
22634
22635
22636
22642
22720
22729
22741
22758
22768
22795
22822
22823
22825
22847
22906
22930
22932

22449
22454
22566
22595
22596
22610
22632
22636
22695
22718
22745
22746
22865
22867
22895
22908
22910
22940
22983
22992
23084
23127
23176
23177
23191
23193
23194
23215
23256
23287
23288
23308
23309
23318
23320
23329
23330
23351
23354
23365
23368
23369
23393
23394
23396
23500
23505
23507
23514
23569
23570
23571
84031B
84077
84509C
84510C
84596B
84596F
84992
85099B
85227
15
21164
21204
21380
21455
21621
21746
21749
21850
22120
22231
22232
22693
23301
23320
82582
18
20755
20758
22113
22114
22302
22372
22374
22554
22555
22556
22557
22632
22835
22867
22996
23005
23356
84029G
8
21683
22469
22622
22623
22776
22782
23570
84945
5
21578
22127
22341
47599A
47599B
29
16045
16054
20719
20728
20973
20974
20975
20981
20984
21932
21934
21935
22371
22372
22376
22382
22383
22609
22610
22662
23207
23208
23209
23240
23388
23389
23390
23391
71496A
74
20668
20712
20713
20752
20973
21158
21159
21213
21231
21248
21588
21625
21642
21644
21810
21811
21818
21819
21822
22094
22097
22130
22154
22187
22208
22211
22

82494L
82578
82580
84029G
84030E
85099B
85152
16
20967
20969
20970
20971
20972
21899
21901
21902
22149
22360
22364
22492
22566
22586
22587
22905
126
10080
15034
15056P
16216
16225
16237
17136A
20682
20971
20972
20982
20984
20996
21014
21034
21098
21158
21159
21162
21175
21181
21311
21326
21340
21358
21367
21368
21591
21592
21622
21703
21820
21829
21849
21850
21851
21915
21931
22086
22091
22112
22114
22139
22158
22162
22189
22197
22403
22411
22473
22597
22605
22607
22608
22616
22623
22627
22629
22639
22725
22728
22729
22730
22735
22737
22771
22789
22818
22835
22952
22990
22991
22992
22998
23101
23103
23133
23165
23198
23202
23203
23268
23270
23293
23295
23314
23322
23332
23333
23353
23355
23356
23357
23388
23389
23390
23461
23492
23504
44234
47503A
47503H
47504H
47504K
47566
47591D
51014A
51014C
51014L
72802A
72807C
75049L
82616C
84012
84031B
84032A
84077
84596B
84596F
84827
85035A
85035C
85036C
85049A
85049G
85150
46
16033
16161P
21231
21232
21411
21523
21733
22060
22151
22418
22457
22

22662
22663
22666
22667
22717
22718
22720
22722
22727
22730
22750
22751
22816
22818
22840
22841
22899
22907
22951
22960
22961
22966
22969
22972
22974
22984
22994
22996
23000
23006
23077
23126
23127
23203
23209
23231
23232
23236
23240
23266
23270
23281
23289
23290
23291
23292
23307
23319
23345
23346
23351
23366
23367
23368
23378
23380
23493
23494
23497
23502
23503
23506
23507
23508
23551
23552
23559
23582
23598
23691
23694
23695
84029G
84077
84519B
85099B
85099F
6
15056N
21212
22417
22699
22938
84991
5
21498
22508
35646
35648
85039A
9
21034
21936
21937
22295
22296
47566
84879
85099F
85123A
23
20969
20971
20972
21260
21892
21906
22142
22144
22147
22149
22273
22274
22489
22491
22494
22565
22566
22568
22569
22570
22620
22621
22945
26
15056BL
15056P
20974
21212
21213
22148
22261
22283
22350
22553
22607
22624
22629
22630
22666
22720
22860
22967
22993
23178
23207
23336
23339
23345
84991
85014B
11
22077
22600
22601
22602
23108
23236
23321
23575
23581
84879
85053
16
21313
21658
22151
22427
2242

22131
22133
22136
22179
22197
22198
22365
22385
22414
22423
22549
22562
22563
22659
22666
22697
22698
22699
22720
22725
22726
22727
22734
22813
22890
22892
22904
22909
22963
22966
22969
22993
23080
23108
23121
23122
23154
23158
23188
23189
23193
23194
23234
23237
23240
23245
23307
23319
23351
23355
23369
23371
23372
23437
23439
23493
23497
23498
23503
23506
23552
47566
48111
48194
84050
84347
84879
85099B
85099C
85099F
85150
8
21624
22087
22178
84313B
84580
84665
84763
85123A
108
16161P
20685
20712
20731
20975
21035
21078
21155
21165
21172
21174
21179
21210
21212
21257
21259
21390
21428
21430
21479
21498
21506
21533
21535
21537
21623
21715
21716
21718
21733
21758
21872
21877
21878
21907
21928
21929
21930
21936
21985
22035
22077
22083
22112
22114
22138
22219
22321
22411
22427
22480
22567
22634
22635
22663
22673
22708
22720
22734
22772
22804
22819
22891
22896
22909
22910
22912
22938
22950
22951
22952
22959
22961
22977
23107
23168
23201
23203
23231
23293
23295
23321
23332
23344
23355
2335

In [41]:
len(user_profiles)

4335

In [42]:
print(user_profiles)

{12346: <1x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 8 stored elements in Compressed Sparse Row format>, 12347: <103x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 593 stored elements in Compressed Sparse Row format>, 12348: <20x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 133 stored elements in Compressed Sparse Row format>, 12349: <72x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 436 stored elements in Compressed Sparse Row format>, 12350: <16x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 82 stored elements in Compressed Sparse Row format>, 12352: <57x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 326 stored elements in Compressed Sparse Row format>, 12353: <4x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 31 stored elements in Compressed Sparse Row format>, 12354: <57x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 338 stored elements in Compressed Sparse Row format>, 12355: <12x3

In [43]:
import numpy
myprofile = user_profiles[12347]
print(myprofile.shape)

l = user_profiles[12347]
l = np.array(l).tolist()

#pd.DataFrame(sorted(zip(tfidf_feature_names, 
                      #  l), key=lambda x: -x[1])[:20], columns=['token', 'relevance'])


(103, 3033)


In [44]:
cosine_similarities = cosine_similarity(user_profiles[12346], tfidf_matrix)
cosine_similarities

array([[0., 0., 0., ..., 0., 0., 0.]])

In [45]:
cosine_similarities.shape

(1, 3659)

In [46]:
print(len(purchases_full_indexed_df.index.unique()))

4335


In [47]:
#Creating the mxn matrix
users = purchases_full_indexed_df.index.unique()
result = []
count=0
len(users)
for user_id in users:
    print("working on user #{}".format(user_id))
    user_product_similarity = cosine_similarity(user_profiles[user_id],tfidf_matrix)
    user_product_similarity = user_product_similarity.mean(axis=0)
    if count == 0:
        result = scipy.sparse.coo_matrix(user_product_similarity)
    else:
        result = scipy.sparse.vstack((result,user_product_similarity))
    count += 1

working on user #12346
working on user #12347
working on user #12348
working on user #12349
working on user #12350
working on user #12352
working on user #12353
working on user #12354
working on user #12355
working on user #12356
working on user #12357
working on user #12358
working on user #12359
working on user #12360
working on user #12361
working on user #12362
working on user #12363
working on user #12364
working on user #12365
working on user #12367
working on user #12370
working on user #12371
working on user #12372
working on user #12373
working on user #12374
working on user #12375
working on user #12377
working on user #12378
working on user #12379
working on user #12380
working on user #12381
working on user #12383
working on user #12384
working on user #12386
working on user #12388
working on user #12390
working on user #12391
working on user #12393
working on user #12394
working on user #12395
working on user #12397
working on user #12398
working on user #12399
working on 

working on user #12793
working on user #12794
working on user #12795
working on user #12797
working on user #12798
working on user #12802
working on user #12808
working on user #12809
working on user #12811
working on user #12812
working on user #12814
working on user #12815
working on user #12816
working on user #12817
working on user #12818
working on user #12820
working on user #12821
working on user #12822
working on user #12823
working on user #12824
working on user #12826
working on user #12827
working on user #12828
working on user #12829
working on user #12830
working on user #12831
working on user #12832
working on user #12833
working on user #12834
working on user #12836
working on user #12837
working on user #12838
working on user #12839
working on user #12840
working on user #12841
working on user #12842
working on user #12843
working on user #12844
working on user #12845
working on user #12847
working on user #12849
working on user #12851
working on user #12852
working on 

working on user #13298
working on user #13299
working on user #13300
working on user #13301
working on user #13302
working on user #13304
working on user #13305
working on user #13307
working on user #13308
working on user #13309
working on user #13310
working on user #13311
working on user #13313
working on user #13314
working on user #13316
working on user #13317
working on user #13318
working on user #13319
working on user #13320
working on user #13321
working on user #13322
working on user #13323
working on user #13324
working on user #13325
working on user #13327
working on user #13328
working on user #13329
working on user #13330
working on user #13332
working on user #13334
working on user #13336
working on user #13338
working on user #13339
working on user #13340
working on user #13341
working on user #13343
working on user #13344
working on user #13345
working on user #13347
working on user #13348
working on user #13349
working on user #13350
working on user #13351
working on 

working on user #13803
working on user #13804
working on user #13805
working on user #13806
working on user #13807
working on user #13808
working on user #13809
working on user #13810
working on user #13811
working on user #13812
working on user #13813
working on user #13814
working on user #13815
working on user #13816
working on user #13817
working on user #13819
working on user #13821
working on user #13822
working on user #13823
working on user #13824
working on user #13826
working on user #13827
working on user #13828
working on user #13831
working on user #13832
working on user #13833
working on user #13835
working on user #13837
working on user #13838
working on user #13841
working on user #13842
working on user #13844
working on user #13845
working on user #13846
working on user #13848
working on user #13849
working on user #13850
working on user #13851
working on user #13853
working on user #13854
working on user #13856
working on user #13858
working on user #13859
working on 

working on user #14295
working on user #14297
working on user #14298
working on user #14299
working on user #14300
working on user #14301
working on user #14304
working on user #14305
working on user #14306
working on user #14307
working on user #14309
working on user #14311
working on user #14312
working on user #14314
working on user #14315
working on user #14317
working on user #14320
working on user #14321
working on user #14323
working on user #14326
working on user #14327
working on user #14329
working on user #14331
working on user #14332
working on user #14333
working on user #14334
working on user #14335
working on user #14336
working on user #14338
working on user #14339
working on user #14340
working on user #14341
working on user #14342
working on user #14344
working on user #14345
working on user #14346
working on user #14348
working on user #14349
working on user #14350
working on user #14351
working on user #14352
working on user #14353
working on user #14354
working on 

...

working on user #16247
working on user #16248
working on user #16249
working on user #16250
working on user #16253
working on user #16255
working on user #16256
working on user #16257
working on user #16258
working on user #16260
working on user #16261
working on user #16265
working on user #16266
working on user #16268
working on user #16270
working on user #16271
working on user #16272
working on user #16274
working on user #16275
working on user #16276
working on user #16278
working on user #16279
working on user #16281
working on user #16282
working on user #16283
working on user #16284
working on user #16287
working on user #16292
working on user #16293
working on user #16295
working on user #16297
working on user #16298
working on user #16302
working on user #16303
working on user #16305
working on user #16306
working on user #16308
working on user #16309
working on user #16311
working on user #16313
working on user #16315
working on user #16316
working on user #16317
working on 

working on user #16748
working on user #16750
working on user #16751
working on user #16752
working on user #16753
working on user #16754
working on user #16755
working on user #16756
working on user #16757
working on user #16758
working on user #16759
working on user #16761
working on user #16762
working on user #16763
working on user #16764
working on user #16765
working on user #16766
working on user #16767
working on user #16768
working on user #16769
working on user #16770
working on user #16771
working on user #16773
working on user #16774
working on user #16775
working on user #16776
working on user #16777
working on user #16778
working on user #16779
working on user #16780
working on user #16781
working on user #16782
working on user #16784
working on user #16788
working on user #16789
working on user #16790
working on user #16791
working on user #16792
working on user #16793
working on user #16794
working on user #16795
working on user #16796
working on user #16800
working on 

working on user #17245
working on user #17247
working on user #17248
working on user #17250
working on user #17251
working on user #17252
working on user #17253
working on user #17254
working on user #17255
working on user #17256
working on user #17259
working on user #17262
working on user #17263
working on user #17265
working on user #17266
working on user #17267
working on user #17268
working on user #17272
working on user #17274
working on user #17277
working on user #17278
working on user #17279
working on user #17282
working on user #17284
working on user #17286
working on user #17287
working on user #17288
working on user #17289
working on user #17290
working on user #17291
working on user #17293
working on user #17295
working on user #17297
working on user #17298
working on user #17299
working on user #17301
working on user #17302
working on user #17303
working on user #17306
working on user #17309
working on user #17311
working on user #17312
working on user #17313
working on 

working on user #17733
working on user #17734
working on user #17735
working on user #17736
working on user #17737
working on user #17738
working on user #17739
working on user #17742
working on user #17744
working on user #17746
working on user #17747
working on user #17749
working on user #17750
working on user #17752
working on user #17754
working on user #17757
working on user #17758
working on user #17759
working on user #17760
working on user #17761
working on user #17763
working on user #17764
working on user #17765
working on user #17767
working on user #17768
working on user #17769
working on user #17770
working on user #17771
working on user #17772
working on user #17774
working on user #17775
working on user #17777
working on user #17779
working on user #17781
working on user #17783
working on user #17785
working on user #17786
working on user #17787
working on user #17788
working on user #17789
working on user #17790
working on user #17791
working on user #17793
working on 

working on user #18231
working on user #18232
working on user #18233
working on user #18235
working on user #18236
working on user #18237
working on user #18239
working on user #18240
working on user #18241
working on user #18242
working on user #18245
working on user #18246
working on user #18248
working on user #18249
working on user #18250
working on user #18251
working on user #18252
working on user #18255
working on user #18257
working on user #18259
working on user #18260
working on user #18261
working on user #18262
working on user #18263
working on user #18265
working on user #18268
working on user #18269
working on user #18270
working on user #18272
working on user #18273
working on user #18274
working on user #18276
working on user #18277
working on user #18278
working on user #18280
working on user #18281
working on user #18282
working on user #18283
working on user #18287


In [48]:
result.shape

(4335, 3659)

In [51]:
content_based_result = result.todense()
content_based_result.shape

(4335, 3659)

In [67]:
content = np.array(content_based_result)
content

array([[0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.01260941, 0.00465927, 0.00575894, ..., 0.        , 0.00425312,
        0.        ],
       [0.00248883, 0.        , 0.00608386, ..., 0.        , 0.03263945,
        0.00916767],
       ...,
       [0.        , 0.        , 0.00343376, ..., 0.        , 0.00524149,
        0.01031749],
       [0.01067502, 0.00712775, 0.01053302, ..., 0.        , 0.00550566,
        0.00284622],
       [0.01065398, 0.00399316, 0.04992605, ..., 0.        , 0.0046747 ,
        0.        ]])

In [73]:
#np.savetxt("content_filter.csv", collab_result, delimiter=",")

## Collaborative Filtering

There are many model-based CF algorithms to recommend items to users such as neural networks, bayerian networks, clustering models, and latent factor models such as Singular Value Decomposition (SVD) and, probabilistic latent semantic analysis. 

### Matrix Factorization: SVD

Latent factor models compress the user-item matrix into a low-dimensional representation in terms of latent factors. One advantage of using this approach is that instead of having a high dimensional matrix containing a large number of missing values, we will be dealing with a much smaller matrix in lower-dimensional space. 

We will be using a popular latent factor model named Singular Value Decomposition (SVD). There are other frameworks such as surprise, mrec, python-recsys that are specific to Collaborative Filters, however, we'll stick with SciPy. We can check our auroc scores as well.

In [21]:
Purchases_df = prop.groupby(['customer_id','product_id'])['value'].mean().reset_index()
print('# of unique customer/item purchases: %d' % len(Purchases_df))
Purchases_df.describe()

# of unique customer/item purchases: 212995


customer_id          value
count  212995.000000  212995.000000
mean    15273.910899       3.490932
std      1710.864276       1.345601
min     12346.000000       0.000000
25%     13862.000000       2.572890
50%     15214.000000       3.666757
75%     16771.000000       4.238515
max     18287.000000      17.362137

In [22]:
#Creating a sparse pivot table with users in rows and items in columns

users_items_pivot_matrix_df = Purchases_df.pivot(index='customer_id',
                                                      columns='product_id',
                                                      values='value').fillna(0)
users_items_pivot_matrix_df.head(100)

product_id      10002  10080  10120  10123C  10124A  10124G  10125  10133  \
customer_id                                                                 
12346        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12347        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12348        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12349        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12350        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12352        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12353        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12354        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12355        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12356        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12357        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12358        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12359        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12360        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12361        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12362        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12363        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12364        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12365        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12367        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12370        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12371        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12372        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12373        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12374        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12375        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12377        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12378        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12379        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12380        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
...               ...    ...    ...     ...     ...     ...    ...    ...   
12432        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12433        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12434        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12435        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12436        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12437        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12438        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12441        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12442        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12444        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12445        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12446        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12447        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12448        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12449        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12450        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12451        3.485427    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12452        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12453        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0

In [23]:
users_items_pivot_matrix = users_items_pivot_matrix_df.as_matrix()
users_items_pivot_matrix[:10]

C:\Users\Prakash14\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  """Entry point for launching an IPython kernel.


array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [24]:
users_ids = list(users_items_pivot_matrix_df.index)
users_ids[:10]

[12346, 12347, 12348, 12349, 12350, 12352, 12353, 12354, 12355, 12356]

In [85]:
matrix_factors = 250
U, sigma, Vt = svds(users_items_pivot_matrix, k = matrix_factors)

In [86]:
U.shape

(4335, 250)

In [87]:
Vt.shape

(250, 3659)

In [88]:
sigma = np.diag(sigma)
sigma.shape

(250, 250)

In [89]:
all_user_predicted_ratings = np.dot(np.dot(U,sigma),Vt)
all_user_predicted_ratings

array([[-0.01627031,  0.0082518 ,  0.00029007, ..., -0.00109396,
         0.00355112, -0.00109396],
       [ 0.27808053,  0.20339193,  0.06910354, ..., -0.00299088,
        -0.00531277, -0.00299088],
       [ 0.09823271,  0.03870828, -0.00477849, ..., -0.00204669,
        -0.00388597, -0.00204669],
       ...,
       [-0.036563  ,  0.04735308,  0.00070612, ...,  0.000669  ,
         0.01199749,  0.000669  ],
       [ 0.13758553, -0.02118097,  0.00159102, ...,  0.00483865,
        -0.00537922,  0.00483865],
       [ 0.08792768,  0.05998682,  0.01717909, ...,  0.00737217,
        -0.00954798,  0.00737217]])

In [90]:
all_user_predicted_ratings.shape

(4335, 3659)

In [91]:
cf_preds_df = pd.DataFrame(all_user_predicted_ratings, 
                           columns = users_items_pivot_matrix_df.columns,
                           index=users_ids).transpose()
cf_preds_df.head(100)

12346     12347     12348     12349     12350     12352  \
product_id                                                               
10002      -0.016270  0.278081  0.098233  0.197215 -0.004796 -0.232889   
10080       0.008252  0.203392  0.038708  0.077534  0.010554  0.068718   
10120       0.000290  0.069104 -0.004778 -0.030964  0.010200 -0.008057   
10123C      0.000248 -0.000456  0.003664 -0.003658 -0.001499 -0.005168   
10124A     -0.000419  0.014638  0.004076 -0.023141 -0.005751  0.003845   
10124G     -0.010780  0.016947  0.021438 -0.013999 -0.000645 -0.016873   
10125       0.086356 -0.067831  0.105127  0.167025 -0.087158 -0.216121   
10133       0.188580  0.624488 -0.009930 -0.218952 -0.026183  0.248716   
10135       0.108397 -0.049029 -0.221122  0.226909  0.032399  0.268608   
11001       0.088621  0.211499  0.288342 -0.109251  0.057654 -0.160020   
15030       0.016425 -0.035923 -0.012357 -0.010515 -0.009047 -0.012229   
15034      -0.004909  0.260761  0.123351  0.004913  0.087570  0.017887   
15036       0.018879 -0.958126  0.357965  0.146039  0.098631 -0.352473   
15039      -0.026058 -0.176935  0.188240 -0.176417  0.052570  0.021185   
15044A      0.038073  0.178055  0.065900  0.318215  0.074635  0.123192   
15044B     -0.050451  0.238279  0.034128 -0.147747  0.100808  0.199997   
15044C      0.047579  0.113217  0.241990  0.039162  0.068635  0.115772   
15044D      0.043962  0.378879  0.331616  0.039165  0.095412  0.167533   
15056BL     0.114300 -0.189629  0.019646  1.103401 -0.143137 -0.214818   
15056N      0.079636 -0.197661  0.085880 -0.483569 -0.114084  0.433987   
15056P     -0.164781  0.360124  0.165020  0.622624 -0.067875  0.178585   
15058A     -0.025320  0.213138 -0.254026 -0.288975 -0.020531  0.249837   
15058B     -0.029654  0.243037  0.074697 -0.185579 -0.023425 -0.084808   
15058C      0.040135  0.064084 -0.065924 -0.235984  0.120431 -0.031981   
15060B      0.018413  0.224336  0.028557  0.246402 -0.025051  0.089468   
16008       0.037138  0.418158  0.066542  0.072823  0.042653 -0.002815   
16010       0.004192  0.002433  0.014223 -0.002377  0.000540 -0.020615   
16011       0.008647  0.021964 -0.083103  0.084447  0.015935  0.042941   
16012      -0.001525  0.048852  0.012999 -0.138657 -0.029665 -0.116894   
16014       0.066787 -0.086669  0.003470  0.264740  0.008693 -0.203385   
...              ...       ...       ...       ...       ...       ...   
16244B     -0.001416  0.015085  0.031291 -0.000357  0.000442 -0.004971   
16248B      0.010656  0.004805  0.016905 -0.055693  0.014583 -0.019242   
16254      -0.003308 -0.008719  0.003179 -0.021120  0.009222  0.014700   
16258A     -0.004316 -0.005824 -0.023834  0.093780  0.034057  0.171151   
16259       0.045058 -0.038398 -0.010615  0.022480 -0.002746 -0.033097   
17001       0.000245  0.000499  0.000289 -0.000515 -0.000031  0.000328   
17003       0.006746 -0.324001  0.292338 -0.074458  0.015745  0.309684   
17007B      0.027269  0.028772  0.016635 -0.019512 -0.010497  0.003978   
17011F     -0.013235  0.056251 -0.024512  0.096204 -0.002767  0.022660   
17012A     -0.016573 -0.022999  0.066271  0.102389  0.030179 -0.036863   
17012B     -0.008360 -0.235038  0.003304  0.214045  0.011814 -0.000484   
17012C     -0.028456  0.028876 -0.056907 -0.035712  0.018367 -0.089168   
17012D      0.143893 -0.093623 -0.157544  0.089412 -0.016699 -0.144025   
17012E      0.010075  0.027593  0.020958  0.033096 -0.006909 -0.048012   
17012F      0.007170 -0.088946 -0.057952  0.026539 -0.011658 -0.123177   
17013D     -0.033754 -0.088436  0.028751  0.131287 -0.018392 -0.009118   
17014A     -0.000204 -0.015930 -0.004004 -0.012313  0.005805 -0.007147   
17021      -0.026252  0.814053 -0.013529  0.062184  0.024505 -0.021131   
17028J     -0.001278 -0.004763  0.001167  0.001715  0.000056 -0.001158   
17038       0.039065 -0.005952  0.026260  0.211723  0.056560 -0.022504   
17084A     -0.010004 -0.036618  0.029674 -0.039689  0.005429 -0.038587   
17084J     -0.00498

In [92]:
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import label_binarize
#users_items_pivot_matrix = label_binarize(users_items_pivot_matrix, classes=[0, 1])
#all_user_predicted_ratings = label_binarize(all_user_predicted_ratings,classes=[0,1])
print (mean_squared_error(users_items_pivot_matrix,all_user_predicted_ratings))

0.07888780767756616


In [84]:
print (mean_squared_error(users_items_pivot_matrix,content_based_result))

0.1876157439998291


We can see that mean squared error wise the collaborative filter actually performs better than the content based filter, as can be expected.  

## Hybrid content based and collaborative recommendation

We can go all caveman and just smash the two matrix together by mutliplying them. However, we know that content based reccommdations are better equiped to overcome the cold start problem. So one method we could undertake is to weight the content based filter to have heavier implications for users that have bought less than 5 unique purchases. 

In [93]:
hybrid = np.multiply(all_user_predicted_ratings,content)

In [94]:
hybrid.shape

(4335, 3659)

In [95]:
print (mean_squared_error(users_items_pivot_matrix,hybrid))

0.18646279848013947


In [72]:
all_user_predicted_ratings

array([[-1.14637326e-02, -2.48879438e-03, -1.85262652e-03, ...,
        -7.73979913e-05, -4.40583047e-04, -7.73979913e-05],
       [ 2.12127948e-01,  4.53974688e-02,  6.89971902e-03, ...,
        -1.11282781e-04,  1.51285041e-03, -1.11282781e-04],
       [ 3.80054512e-02,  2.37319526e-02, -1.57698300e-03, ...,
        -3.56175006e-04,  5.44404982e-04, -3.56175006e-04],
       ...,
       [-5.38133098e-03,  2.22894610e-03, -2.72147457e-03, ...,
         2.72045816e-04,  2.19187664e-04,  2.72045816e-04],
       [ 9.31312366e-02,  2.33848378e-02,  1.50648374e-02, ...,
         8.21456300e-04, -2.35515801e-03,  8.21456300e-04],
       [ 6.44299971e-02,  2.01267204e-02,  1.31997385e-02, ...,
         2.48152091e-04,  4.72463937e-03,  2.48152091e-04]])

In [73]:
content

array([[0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.01260941, 0.00465927, 0.00575894, ..., 0.        , 0.00425312,
        0.        ],
       [0.00248883, 0.        , 0.00608386, ..., 0.        , 0.03263945,
        0.00916767],
       ...,
       [0.        , 0.        , 0.00343376, ..., 0.        , 0.00524149,
        0.01031749],
       [0.01067502, 0.00712775, 0.01053302, ..., 0.        , 0.00550566,
        0.00284622],
       [0.01065398, 0.00399316, 0.04992605, ..., 0.        , 0.0046747 ,
        0.        ]])

In [169]:
user_purchases = prop.groupby('customer_id')['quantity'].size().sort_values(ascending=False).reset_index()
user_purchases.describe()

customer_id     quantity
count   4335.000000  4335.000000
mean   15298.780392    71.945559
std     1722.075082   176.697865
min    12346.000000     1.000000
25%    13811.500000    14.000000
50%    15297.000000    32.000000
75%    16778.500000    79.000000
max    18287.000000  5886.000000

In [108]:
users_low_purchases = user_purchases[user_purchases.quantity<5]
users_low_purchases.describe()

customer_id    quantity
count    291.000000  291.000000
mean   15380.144330    2.419244
std     1734.977313    1.148991
min    12346.000000    1.000000
25%    13947.500000    1.000000
50%    15316.000000    2.000000
75%    16820.000000    3.000000
max    18273.000000    4.000000

291 users with purchases less than 5. These can be great candidates for content based recommendations

In [109]:
users_low_purchases.head()

customer_id  quantity
4044        18246         4
4045        17900         4
4046        12401         4
4047        12403         4
4048        17844         4

In [114]:
check = cf_preds_df.transpose()
check

product_id     10002     10080     10120    10123C    10124A    10124G  \
12346      -0.016270  0.008252  0.000290  0.000248 -0.000419 -0.010780   
12347       0.278081  0.203392  0.069104 -0.000456  0.014638  0.016947   
12348       0.098233  0.038708 -0.004778  0.003664  0.004076  0.021438   
12349       0.197215  0.077534 -0.030964 -0.003658 -0.023141 -0.013999   
12350      -0.004796  0.010554  0.010200 -0.001499 -0.005751 -0.000645   
12352      -0.232889  0.068718 -0.008057 -0.005168  0.003845 -0.016873   
12353       0.005724  0.014113  0.004228 -0.000781 -0.002138 -0.005177   
12354      -0.205327 -0.185962 -0.032555  0.012470  0.004686  0.020225   
12355      -0.036167  0.075015 -0.000884 -0.000156 -0.006759  0.000807   
12356       0.062621  0.060604 -0.010512  0.001655  0.006295 -0.009969   
12357      -0.112823  0.223598 -0.026307 -0.003080 -0.042492  0.012237   
12358       0.069979  0.029438 -0.024017 -0.002229 -0.000603 -0.007533   
12359      -0.018199 -0.181165 -0.000163 -0.008602  0.011877  0.027889   
12360       0.218860  0.092151  0.079359  0.009488 -0.006487 -0.036442   
12361       0.104840 -0.040225 -0.002092 -0.000927 -0.001304 -0.006624   
12362       0.232289  0.055462 -0.040231 -0.002792 -0.019315 -0.024455   
12363      -0.091532 -0.061762 -0.014920 -0.000802 -0.006229 -0.009133   
12364       0.157450  0.126086 -0.008801  0.002410 -0.009322 -0.026002   
12365      -0.116877  0.040644 -0.008529  0.003343  0.004578  0.006888   
12367      -0.007075 -0.013803  0.007285  0.000574  0.005161  0.001001   
12370      -0.074916  0.091144  0.020030  0.014619  0.011429  0.017526   
12371      -0.174364 -0.050053  0.041125  0.001764  0.018658 -0.022596   
12372       0.134645 -0.016883 -0.013674 -0.002545  0.005412 -0.014889   
12373       0.082171 -0.055447 -0.010182 -0.003427 -0.010257 -0.007321   
12374       0.000413  0.059833 -0.015907  0.002331  0.001312 -0.004257   
12375       0.031072 -0.039400 -0.007422 -0.000406 -0.005225 -0.004870   
12377       0.199827  0.022856  0.016463 -0.003442  0.013962 -0.006109   
12378      -0.076590 -0.104047 -0.025589  0.022712  0.033008 -0.011109   
12379       0.131059 -0.080927 -0.021313 -0.000035 -0.002844 -0.010405   
12380       0.184327 -0.023427 -0.016124 -0.007224 -0.014067  0.001410   
...              ...       ...       ...       ...       ...       ...   
18242       0.168071  0.015383 -0.040149 -0.004670 -0.003710 -0.011966   
18245      -0.111213  0.057351 -0.015267  0.001304  0.006220 -0.026414   
18246       0.001967  0.021182 -0.013636 -0.000730  0.004113  0.005297   
18248      -0.061982 -0.090190  0.002026  0.000391 -0.004997 -0.015000   
18249       0.032792  0.028019  0.004594  0.000268  0.005931  0.008232   
18250       0.087353 -0.028106 -0.017141 -0.003086  0.003545  0.007533   
18251       0.041186 -0.060955 -0.052254  0.006242  0.010388 -0.005556   
18252       0.126757  0.003254 -0.012129 -0.001683  0.006706  0.007921   
18255       0.020650 -0.002844  0.002847  0.001031 -0.000497 -0.001593   
18257      -0.244414 -0.031462  0.024616 -0.007002 -0.002209  0.009175   
18259      -0.042469 -0.111298 -0.036553 -0.004497  0.023272 -0.001750   
18260       0.225688  0.002810 -0.004413  0.011864 -0.019540 -0.020877   
18261      -0.093283  0.019292  0.033516 -0.001226 -0.006373  0.009336   
18262       0.060908 -0.017370  0.000835 -0.001543  0.005835  0.014547   
18263       0.005976  0.097770  0.092419 -0.000556  0.000595  0.024096   
18265       0.200342  0.002618  0.004843 -0.007802 -0.000583  0.001954   
18268      -0.002339  0.000716 -0.001078 -0.000140  0.000277  0.001272   
18269       0.071520 -0.025198  0.004616 -0.000380  0.007266  0.001570   
18270      -0.017911 -0.016287 -0.002740  0.000254 -0.003236 -0.004659   
18272      -0.120299 -0.031811 -0.065208 -0.009488 -0.028198 -0.006701   
18273       0.002267  0.001027 -0.000674 -0.000068 -0.000239 -0.000801   
18274      -0.032592  0.007550  0.003935  0.002420  0.006033  0.000743   
1827

In [119]:
check.index.values

array([12346, 12347, 12348, ..., 18282, 18283, 18287], dtype=int64)

In [124]:
hybrid_matrix = all_user_predicted_ratings
row_number = 0
count = 0
for i in check.index.values:
    for customer_id in users_low_purchases['customer_id']:
        if i == customer_id:
            hybrid_matrix[row_number] = content_based_result[row_number]
            count +=1
            print(hybrid_matrix[row_number])
    row_number += 1

[0. 0. 0. ... 0. 0. 0.]
[0.05385289 0.         0.         ... 0.0975574  0.         0.        ]
[0.        0.        0.        ... 0.0390523 0.        0.       ]
[0.         0.03701079 0.03056005 ... 0.         0.01066636 0.        ]
[0.01837574 0.02601901 0.         ... 0.         0.         0.        ]
[0.0165922  0.         0.03983578 ... 0.         0.01410134 0.06141489]
[0.         0.         0.         ... 0.         0.01668215 0.        ]
[0. 0. 0. ... 0. 0. 0.]
[0.         0.02616608 0.02281794 ... 0.         0.         0.        ]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0.01689179 0.06827778 0.         ... 0.         0.01175124 0.        ]
[0.03378357 0.04783563 0.         ... 0.         0.         0.        ]
[0.         0.         0.05402647 ... 0.         0.         0.        ]
[0.        0.        0.        ... 0.        0.0104812 0.       ]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0.09365081 0.         0.         ... 0.         0.         0.        ]
[0. 

[0. 0. 0. ... 0. 0. 0.]
[0.07392224 0.10466973 0.         ... 0.         0.         0.        ]
[0.3995831 0.        0.        ... 0.        0.        0.       ]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0.0911488  0.04703701 0.         ... 0.         0.         0.        ]
[0.         0.         0.05779829 ... 0.         0.         0.        ]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0.03208798 0.04543477 0.         ... 0.         0.02502323 0.        ]
[0.06417596 0.09086955 0.         ... 0.         0.         0.        ]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0.031656 0.       0.       ... 0.       0.       0.      ]
[0. 0. 0. ... 0. 0. 0.]
[0.16047869 0.03805961 0.         ... 0.         0.         0.        ]
[0. 0. 0. ... 0. 0. 0.]
[0.        0.        0.        ... 0.1323117 0.        0.       ]
[0.07567623 0.         0.         ... 0.         0.02498784 0.        ]
[0.09419846 0.  

In [125]:
print(count)

291


In [121]:
hybrid_matrix.shape

(4335, 3659)

In [122]:
print (mean_squared_error(users_items_pivot_matrix,hybrid_matrix))

0.07945429417589428


### Another way of hybridization: Create a weighting based on how many items the user has bought. That weighting is then used to decide how much of an influence either content based or collaborative filter will have. 

In [126]:
user_purchases.head(10)

customer_id  quantity
0        17841      5886
1        14911      4474
2        14096      3921
3        12748      3618
4        14606      2084
5        15311      1869
6        14646      1572
7        13089      1426
8        13263      1307
9        14298      1291

In [170]:
#We divide everything by 5886
user_purchases2 = user_purchases
user_purchases2['quantity'] = np.log(user_purchases2['quantity']) #user_purchases['quantity']/5886

customer_id  quantity
0        17841  8.680332
1        14911  8.406038
2        14096  8.274102
3        12748  8.193677
4        14606  7.642044

In [173]:
user_purchases2.set_index('customer_id')

quantity
customer_id          
17841        8.680332
14911        8.406038
14096        8.274102
12748        8.193677
14606        7.642044
15311        7.533159
14646        7.360104
13089        7.262629
13263        7.175490
14298        7.163172
15039        7.072422
14156        6.953684
18118        6.949856
14159        6.824374
14796        6.806829
16033        6.774224
14769        6.729824
14056        6.714171
15005        6.710523
13081        6.703188
14527        6.665684
14456        6.645091
17511        6.603944
16549        6.587550
15555        6.575076
15719        6.558198
16931        6.526495
17811        6.463029
18283        6.447306
14505        6.447306
...               ...
16144        0.000000
16148        0.000000
18133        0.000000
14351        0.000000
17956        0.000000
16754        0.000000
12603        0.000000
14576        0.000000
13256        0.000000
15510        0.000000
13270        0.000000
17102        0.000000
15524        0.000000
18174        0.000000
13298        0.000000
15562        0.000000
13302        0.000000
13307        0.000000
16990        0.000000
13366        0.000000
15657        0.000000
13391        0.000000
14424        0.000000
16953        0.000000
16881        0.000000
15668        0.000000
13514        0.000000
17986        0.000000
16765        0.000000
12346        0.000000

[4335 rows x 1 columns]

In [148]:
len(content_based_result)

4335

In [183]:
hybrid_matrix_weighted = all_user_predicted_ratings
row_number = 0
count = 0
for i in check.index.values:
    for customer in user_purchases2['customer_id']:
        print(customer)
        if customer == i:
            weight = user_purchases2.get_value(customer,'quantity')
            hybrid_matrix_weighted[row_number] = np.multiply((weight*hybrid_matrix_weighted[row_number]), ((1-weight)*content_based_result[row_number]))
            count = count +1
            print(hybrid_matrix_weighted[i])
   

17841
14911
14096
12748
14606
15311
14646
13089
13263
14298
15039
14156
18118
14159
14796
16033
14769
14056
15005
13081
14527
14456
17511
16549
15555
15719
16931
17811
18283
14505
17338
12415
17675
13137
15159
17757
12921
16904
16241
17920
17735
16923
15529
15547
16764
12681
14502
16729
13098
16360
14415
16713
13969
15856
14088
14194
15993
13230
15861
16910
15023
17602
17238
13694
17611
14667
12867
16686
14367
14534
15498
15640
15998
15358
17059
16161
17231
17337
17346
13319
18069
17315
13408
17954
12682
18041
15867
17220
14895
14049
17365
16558
14730
15033
15356
17139
12621
14085
12540
13668
13018
16746
16712
13097
13451
17107
17581
13268
15601
15021
15044
16813
15078
13521
12474
13069
12567
12433
12841
17364
14562
13488
13767
15615
18109
18102
14704
17340
17799
13458
14546
13004
15752
13050
16710
14684
17243
16984
17377
12637
17576
17758
18122
14936
15034
17530
16843
18116
15443
15061
17706
14849
13985
12471
12720
14432
17865
16422
16426
14587
16745
15249
18055
14702
14800
14903
1781

17624
12913
14129
14359
16554
15325
13439
15579
16954
13140
14550
13363
17169
14815
15434
17649
17771
14594
15681
13662
17096
15489
14389
15211
15550
13243
16930
14716
17564
15274
14918
14953
17432
14488
17885
13308
17299
14508
12550
12939
17007
18236
15807
12752
14959
14875
17303
14731
15437
15028
15079
15253
15611
15132
15238
16624
16480
12640
14077
17848
12680
17431
16833
15900
13760
12794
16204
16734
16494
12857
16893
17594
12701
16235
14352
13692
18005
17090
18248
13278
14167
18126
12488
14154
18265
14152
17552
17521
16536
15980
17579
13575
14625
17505
14050
13016
15239
17383
16493
14002
16270
14690
17227
18127
16333
16415
16406
16573
14128
16411
15829
15658
13563
17839
16594
17795
17793
15626
12372
17772
17874
17739
14409
13568
13656
13790
12642
17358
14770
17860
13109
15507
15095
17937
14725
17976
13291
13900
16419
14381
17984
17051
17002
14261
16774
14880
13495
17527
14138
16020
13730
12878
18061
15883
14862
16539
15467
17144
16718
13940
13376
14412
18181
14790
18171
18045
1282

16313
17239
17253
16281
14972
16850
15355
13781
12623
12715
14784
16810
13666
13411
16660
17824
14491
15254
15607
16761
16690
15234
17789
13479
16697
16952
15637
13874
13169
14339
14618
16217
17312
13990
14333
13146
13972
17234
15793
14847
13932
12812
16325
12604
12787
15732
17359
15087
17668
12650
15942
17475
12962
18108
15504
14557
12355
17895
17572
15127
14581
18193
12882
16119
13045
18074
13226
16215
12750
18262
13329
13328
14974
12519
13754
16473
15333
14666
17854
16451
17011
16510
16997
13272
17694
17684
15045
18010
14385
14434
16587
17142
17973
14761
17506
17742
12373
14885
13348
14932
12953
15119
12990
15124
13033
17670
13043
14870
14964
17978
17176
14828
17877
15224
16957
12837
15174
17969
17939
17862
14947
17040
14863
17600
13489
14799
14798
16961
15598
16125
13792
13805
15497
15307
14523
16302
15516
16450
13946
15363
15692
16689
15263
16321
16338
14355
15667
14416
13889
18215
14236
15895
15277
15578
13803
13978
14624
18129
14484
16123
13711
16149
16157
14476
16105
15609
1468

C:\Users\Prakash14\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: FutureWarning: get_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead
  


KeyError: 12346

In [178]:
user_purchases2.index.values

array([   0,    1,    2, ..., 4332, 4333, 4334], dtype=int64)